In [1]:
using SpiDy
using NPZ
using DataFrames
using CSV
using ProgressMeter
using Random
using Statistics
using LinearAlgebra
using Plots

########################
########################

Δt = 1
N = 200
tspan = (0., N*Δt)
saveat = (0:1:N)*Δt
α = 0.16
ω0 = 1.4
Γ = 0.5
J = LorentzianSD(α, ω0, Γ) # coloring the noise
matrix = AnisoCoupling([-sin(π/4) 0. 0. # coupling to the environment
                        0. 0. 0.
                        cos(π/4) 0. 0.]);
T = .01
noise = ClassicalNoise(T);

nspin = 1 # number of spins

s0 = zeros(3*nspin)
for i in 1:nspin
    ϵ = 0.1
    s0tmp = [ϵ*rand(), ϵ*rand(), -1]
    s0[1+(i-1)*3:3+(i-1)*3] = s0tmp./norm(s0tmp)
end
J0 = 1.
JH = Nchain(nspin, J0)

nruns = 1000


1000

In [ ]:
println("Starting...")
progress = Progress(nruns);

sols = zeros(nruns, length(saveat), 3*nspin)

Threads.@threads for i in 1:nruns
    bfields = [bfield(N, Δt, J, noise),
               bfield(N, Δt, J, noise),
               bfield(N, Δt, J, noise)];
    sol = diffeqsolver(s0, tspan, J, bfields, matrix; JH=JH, saveat=saveat);
    sols[i, :, :] = transpose(sol[:, :])
    next!(progress)
end

solavg = mean(sols, dims=1)[1, :, :];
solstd = std(sols, dims=1)[1, :, :];

Starting...


Progress:   7%|██▊                                      |  ETA: 0:13:09

In [ ]:
plot(saveat, solavg[:, 1], ribbon=solstd[:, 1])

In [ ]:
plot(saveat, solavg[:, 2], ribbon=solstd[:, 2])

In [ ]:
plot(saveat, solavg[:, 3], ribbon=solstd[:, 3])

In [ ]:
projected = zeros(nruns, length(saveat), 2)

normalized_avg = eachrow(solavg) |> x -> normalize(x)

for i in 1:length(saveat)
    n = normalized_avg[i, :][1]

    u = normalize(cross(n, [0,0,1]))
    v = cross(u, n)

    for j in 1:nruns
        b = sols[j, i, :]
        proj = dot(b, n) * n
        b_ort = b - proj

        projected[j, i, 1] = dot(u,b)
        projected[j, i, 2] = dot(v,b)
    end
end

In [ ]:
histogram(projected[:, 197, 1])

In [ ]:
histogram(projected[:, 20, 2])

In [ ]:
function nth_moment(data, N)
    return mean(data .^ N)
end

In [ ]:
using HypothesisTests

In [ ]:
JB = zeros(N)
for i in 10:N
    JB[i] = HypothesisTests.JarqueBeraTest(projected[:, i, 1]).JB
end

In [ ]:
plot(10:N, JB[10:N])

In [ ]:
HypothesisTests.JarqueBeraTest(projected[:, 197, 1])

In [ ]:
HypothesisTests.JarqueBeraTest(projected[:, 200, 1])